In [1]:
import requests
import json
import pandas as pd
import time
import random

In [2]:
# Initialize an empty list to store each batch of matches data
all_matches = []

# Loop over drillDownTagIds ranges in steps of 1000
for start in range(0, 20000, 1000):
    # Generate a comma-separated string of drillDownTagIds for the current range
    drilldown_ids = ','.join(str(i) for i in range(start, start + 1000))

    # Define the request URL
    url = (
        f"https://content.toto.nl/content-service/api/v1/q/event-list?"
        "startTimeFrom=2024-11-10T23:00:00Z&"
        "startTimeTo=2024-11-21T22:59:59Z&"
        "liveNow=false&"
        "maxEvents=190&"
        "orderEventsBy=popularity&"
        "orderMarketsBy=displayOrder&"
        "marketSortsIncluded=--,CS,DC,DN,HH,HL,MH,MR,WH&"
        "marketGroupTypesIncluded=CUSTOM_GROUP,DOUBLE_CHANCE,DRAW_NO_BET,MATCH_RESULT,"
        "MATCH_WINNER,MONEYLINE,ROLLING_SPREAD,ROLLING_TOTAL,STATIC_SPREAD,STATIC_TOTAL&"
        "eventSortsIncluded=MTCH&"
        "includeChildMarkets=true&"
        "prioritisePrimaryMarkets=true&"
        "includeCommentary=true&"
        "includeMedia=true&"
        f"drilldownTagIds={drilldown_ids}&"
        "categoryCode=tennis&"  # Specify the desired category
        "lang=nl-NL&"
        "channel=I"
    )

    # Headers for the request
    headers = {
        'accept': 'application/json',
        'accept-language': 'en-US,en;q=0.9,nl;q=0.8',
    }

    # Make the request
    response = requests.get(url, headers=headers)

    # Parse the JSON response
    data = response.json()

    # Extract match data if available
    matches = []
    for event in data.get('data', {}).get('events', []):
        match = {
            "event_id": event.get("id"),
            "match_name": event.get("name"),
            "start_time": event.get("startTime"),
            "home_team": next((team['name'] for team in event.get('teams', []) if team['side'] == "HOME"), None),
            "away_team": next((team['name'] for team in event.get('teams', []) if team['side'] == "AWAY"), None),
            "competition": event.get('type', {}).get('name'),
            "country": event.get('class', {}).get('name'),
            "sport": event.get('category', {}).get('name'),
        }
        
        # Extract odds if available
        outcomes = event.get("markets", [{}])[0].get("outcomes", [])
        match["home_odds"] = next((outcome['prices'][0]['decimal'] for outcome in outcomes if outcome.get('subType') == "H"), None)
        match["away_odds"] = next((outcome['prices'][0]['decimal'] for outcome in outcomes if outcome.get('subType') == "A"), None)
        
        matches.append(match)

    # Add the batch of matches to the all_matches list
    all_matches.extend(matches)

    # Sleep for a random duration between 1 and 4 seconds, with variability of 0.1 ms
    time.sleep(random.uniform(1, 2.001))

# Combine all match data into a single DataFrame
final_matches_df = pd.DataFrame(all_matches)

# Display the resulting DataFrame
final_matches_df

event_id                                 match_name  \
0     5120927  Deportivo Riestra Afbc vs Vélez Sarsfield   
1     5120933             CA Tigre vs Defensa Y Justicia   
2     5120928              Atletico Lanus vs CA Platense   
3     5339873               Deportivo La Coruna vs Eibar   
4     5699848                        Frankrijk vs Israël   
...       ...                                        ...   
1315  5955112            Milan Kolar vs Yurii Holovatiuk   
1316  5955117                Milan Smrcek vs Milan Kolar   
1317  5955124           Milan Smrcek vs Yurii Holovatiuk   
1318  5955069    Miroslav Nejedly vs Marek Wiederlechner   
1319  5955065    Miroslav Nejedly vs Milan Hvojka Senior   

                start_time               home_team            away_team  \
0     2024-11-11T19:00:00Z  Deportivo Riestra Afbc      Vélez Sarsfield   
1     2024-11-11T21:45:00Z                CA Tigre   Defensa Y Justicia   
2     2024-11-11T21:45:00Z          Atletico Lanus          CA Platense   
3     2024-11-11T19:30:00Z     Deportivo La Coruna                Eibar   
4     2024-11-14T19:45:00Z               Frankrijk               Israël   
...                    ...                     ...                  ...   
1315  2024-11-13T01:00:00Z             Milan Kolar     Yurii Holovatiuk   
1316  2024-11-13T02:30:00Z            Milan Smrcek          Milan Kolar   
1317  2024-11-12T23:30:00Z            Milan Smrcek     Yurii Holovatiuk   
1318  2024-11-12T08:00:00Z        Miroslav Nejedly  Marek Wiederlechner   
1319  2024-11-12T09:30:00Z        Miroslav Nejedly  Milan Hvojka Senior   

                  competition     country        sport  home_odds  away_odds  
0        Argentinië Superliga  Argentinië      Voetbal       6.50       1.54  
1        Argentinië Superliga  Argentinië      Voetbal       2.20       3.15  
2        Argentinië Superliga  Argentinië      Voetbal       2.20       3.65  
3     Spanje Segunda Division      Spanje      Voetbal       1.71       4.75  
4         UEFA Nations League    Europees      Voetbal       1.13      20.00  
...                       ...         ...          ...        ...        ...  
1315           Czech Liga Pro    Tsjechië  Tafeltennis       1.91       1.80  
1316           Czech Liga Pro    Tsjechië  Tafeltennis       1.61       2.20  
1317           Czech Liga Pro    Tsjechië  Tafeltennis       1.61       2.20  
1318           Czech Liga Pro    Tsjechië  Tafeltennis       2.60       1.44  
1319           Czech Liga Pro    Tsjechië  Tafeltennis       1.83       1.83  

[1320 rows x 10 columns]

In [3]:
final_matches_df

event_id                                 match_name  \
0     5120927  Deportivo Riestra Afbc vs Vélez Sarsfield   
1     5120933             CA Tigre vs Defensa Y Justicia   
2     5120928              Atletico Lanus vs CA Platense   
3     5339873               Deportivo La Coruna vs Eibar   
4     5699848                        Frankrijk vs Israël   
...       ...                                        ...   
1315  5955112            Milan Kolar vs Yurii Holovatiuk   
1316  5955117                Milan Smrcek vs Milan Kolar   
1317  5955124           Milan Smrcek vs Yurii Holovatiuk   
1318  5955069    Miroslav Nejedly vs Marek Wiederlechner   
1319  5955065    Miroslav Nejedly vs Milan Hvojka Senior   

                start_time               home_team            away_team  \
0     2024-11-11T19:00:00Z  Deportivo Riestra Afbc      Vélez Sarsfield   
1     2024-11-11T21:45:00Z                CA Tigre   Defensa Y Justicia   
2     2024-11-11T21:45:00Z          Atletico Lanus          CA Platense   
3     2024-11-11T19:30:00Z     Deportivo La Coruna                Eibar   
4     2024-11-14T19:45:00Z               Frankrijk               Israël   
...                    ...                     ...                  ...   
1315  2024-11-13T01:00:00Z             Milan Kolar     Yurii Holovatiuk   
1316  2024-11-13T02:30:00Z            Milan Smrcek          Milan Kolar   
1317  2024-11-12T23:30:00Z            Milan Smrcek     Yurii Holovatiuk   
1318  2024-11-12T08:00:00Z        Miroslav Nejedly  Marek Wiederlechner   
1319  2024-11-12T09:30:00Z        Miroslav Nejedly  Milan Hvojka Senior   

                  competition     country        sport  home_odds  away_odds  
0        Argentinië Superliga  Argentinië      Voetbal       6.50       1.54  
1        Argentinië Superliga  Argentinië      Voetbal       2.20       3.15  
2        Argentinië Superliga  Argentinië      Voetbal       2.20       3.65  
3     Spanje Segunda Division      Spanje      Voetbal       1.71       4.75  
4         UEFA Nations League    Europees      Voetbal       1.13      20.00  
...                       ...         ...          ...        ...        ...  
1315           Czech Liga Pro    Tsjechië  Tafeltennis       1.91       1.80  
1316           Czech Liga Pro    Tsjechië  Tafeltennis       1.61       2.20  
1317           Czech Liga Pro    Tsjechië  Tafeltennis       1.61       2.20  
1318           Czech Liga Pro    Tsjechië  Tafeltennis       2.60       1.44  
1319           Czech Liga Pro    Tsjechië  Tafeltennis       1.83       1.83  

[1320 rows x 10 columns]

In [69]:
# import requests

# # Generate a comma-separated string of drillDownTagIds between 11000 and 12999
# drilldown_ids = ','.join(str(i) for i in range(0, 1000))

# url = (
#     f"https://content.toto.nl/content-service/api/v1/q/event-list?"
#     "startTimeFrom=2024-11-10T23:00:00Z&"
#     "startTimeTo=2024-11-21T22:59:59Z&"
#     "liveNow=false&"
#     "maxEvents=250&"
#     "orderEventsBy=popularity&"
#     "orderMarketsBy=displayOrder&"
#     "marketSortsIncluded=--,CS,DC,DN,HH,HL,MH,MR,WH&"
#     "marketGroupTypesIncluded=CUSTOM_GROUP,DOUBLE_CHANCE,DRAW_NO_BET,MATCH_RESULT,"
#     "MATCH_WINNER,MONEYLINE,ROLLING_SPREAD,ROLLING_TOTAL,STATIC_SPREAD,STATIC_TOTAL&"
#     "eventSortsIncluded=MTCH&"
#     "includeChildMarkets=true&"
#     "prioritisePrimaryMarkets=true&"
#     "includeCommentary=true&"
#     "includeMedia=true&"
#     f"drilldownTagIds={drilldown_ids}&"  # Generated drilldown tag IDs
#     "categoryCode=tennis&"  # Specify the desired category
#     "lang=nl-NL&"
#     "channel=I"
# )

# headers = {
#     'accept': 'application/json',
#     'accept-language': 'en-US,en;q=0.9,nl;q=0.8',
# }

# response = requests.get(url, headers=headers)

# # Parsing the response
# data = response.json()

# # Display the JSON structure for verification
# print(data)

{'data': {'events': [{'id': '5120927', 'externalIds': [{'id': '10954279', 'provider': 'betgenius'}, {'id': 'sr:match:46657169', 'provider': 'betradar'}], 'extKey': None, 'retailCode': None, 'name': 'Deportivo Riestra Afbc vs Vélez Sarsfield', 'active': True, 'displayed': True, 'status': 'ACTIVE', 'displayOrder': -65, 'popularityOrder': 0, 'channels': ['P', 'A', 'R', 'T', 'X', 'I', 'M', 'O'], 'sortCode': 'MTCH', 'startTime': '2024-11-11T19:00:00Z', 'started': False, 'liveNow': False, 'liveBettingAvailable': True, 'resulted': False, 'settled': False, 'cashoutAvailable': True, 'sportId': '17', 'competitionDrilldownTagId': '2736', 'raceNumber': 0, 'venue': None, 'isVoid': False, 'blurb': None, 'fixedOddsAvailable': True, 'rcpAvailable': True, 'statisticsAvailable': False, 'neutralVenue': False, 'meeting': None, 'teams': [{'id': None, 'side': 'HOME', 'name': 'Deportivo Riestra Afbc', 'alternativeNames': [{'type': 'FULL', 'value': 'Deportivo Riestra Afbc'}], 'code': None, 'externalId': None,

In [80]:
# # Initialize an empty list to collect match data
# matches = []

# # Extract match details from each event
# for event in data['data']['events']:
#     match = {
#         "event_id": event.get("id"),
#         "match_name": event.get("name"),
#         "start_time": event.get("startTime"),
#         "home_team": next((team['name'] for team in event['teams'] if team['side'] == "HOME"), None),
#         "away_team": next((team['name'] for team in event['teams'] if team['side'] == "AWAY"), None),
#         "competition": event['type']['name'],
#         "country": event['class']['name'],
#         "sport": event['category']['name'],
#     }
    
#     # Extract odds, if available
#     outcomes = event.get("markets", [{}])[0].get("outcomes", [])
#     if outcomes:
#         match["home_odds"] = next((outcome['prices'][0]['decimal'] for outcome in outcomes if outcome['subType'] == "H"), None)
#         match["away_odds"] = next((outcome['prices'][0]['decimal'] for outcome in outcomes if outcome['subType'] == "A"), None)
    
#     matches.append(match)

# # Convert the match list to a DataFrame
# matches_df = pd.DataFrame(matches)

# # Display the resulting DataFrame
# matches_df

In [ ]:
# url = "https://content.toto.nl/content-service/api/v1/q/popular-bets-event-list?minPrice=1.25&maxPrice=9.90&combinable=true&numOutcomes=3&startTimeFrom=2024-11-09T13%3A32%3A35Z&startTimeTo=2024-12-10T13%3A32%3A35Z&marketSortsIncluded=HH%2CMR&lang=nl-NL&channel=I"

# payload = {}
# headers = {
#   'accept': 'application/json',
#   'Cookie': 'incap_ses_1581_2280942=FvpNPI919nl1UsyZNNfwFR6GL2cAAAAA8yX5UHfYkaWD/ax05SY+Jg==; visid_incap_2280942=CzAo1Y6yTMa654jo8RfVRtBiL2cAAAAAQkIPAAAAAAAE7rpFtkP20364qTw5VQQQ'
# }

# response = requests.request("GET", url, headers=headers, data=payload)

# match_data = json.loads(response.text)


In [81]:
# # Initialize an empty list to collect match data
# matches = []

# # Extract match details from each event
# for event in match_data['data']['events']:
#     match = {
#         "event_id": event.get("id"),
#         "match_name": event.get("name"),
#         "start_time": event.get("startTime"),
#         "home_team": next((team['name'] for team in event['teams'] if team['side'] == "HOME"), None),
#         "away_team": next((team['name'] for team in event['teams'] if team['side'] == "AWAY"), None),
#         "competition": event['type']['name'],
#         "country": event['class']['name'],
#         "sport": event['category']['name'],
#     }
    
#     # Extract odds, if available
#     outcomes = event.get("markets", [{}])[0].get("outcomes", [])
#     if outcomes:
#         match["home_odds"] = next((outcome['prices'][0]['decimal'] for outcome in outcomes if outcome['subType'] == "H"), None)
#         match["away_odds"] = next((outcome['prices'][0]['decimal'] for outcome in outcomes if outcome['subType'] == "A"), None)
    
#     matches.append(match)

# # Convert the match list to a DataFrame
# matches_df = pd.DataFrame(matches)

# # Display the resulting DataFrame
# matches_df

In [ ]:
import requests
import time
import random
import pandas as pd

# Initialize an empty list to accumulate all data
all_data = []

# Set batch size
batch_size = 100

# Loop over event_ids in batches of 500
for i in range(0, len(final_matches_df['event_id']), batch_size):
    # Get a batch of event_ids
    batch_ids = final_matches_df['event_id'][i:i + batch_size]
    
    # Concatenate event_ids for the URL
    event_ids_str = ','.join(map(str, batch_ids))
    
    # Define the URL for the current batch
    url = (
        f"https://content.toto.nl/content-service/api/v1/q/events-by-ids?"
        f"eventIds={event_ids_str}&"
        "includeChildMarkets=true&includeCollections=true&includePriorityCollectionChildMarkets=true&"
        "includePriceHistory=false&includeCommentary=true&includeIncidents=false&includeRace=false&"
        "includePools=false&includeNonFixedOdds=false&lang=nl-NL&channel=I"
    )
    
    headers = {
        'accept': 'application/json',
        'accept-language': 'en-US,en;q=0.9,nl;q=0.8',
        'Cookie': 'incap_ses_1581_2280942=FvpNPI919nl1UsyZNNfwFR6GL2cAAAAA8yX5UHfYkaWD/ax05SY+Jg==; visid_incap_2280942=CzAo1Y6yTMa654jo8RfVRtBiL2cAAAAAQkIPAAAAAAAE7rpFtkP20364qTw5VQQQ'
    }
    
    # Send request
    response = requests.get(url, headers=headers)
    json_data = response.json()

    # Initialize lists to store the data for this batch
    event_ids = []
    event_names = []
    market_names = []
    outcome_names = []
    odds_decimal = []
    prices_numerator = []
    prices_denominator = []
    outcome_types = []
    outcome_subtypes = []

    # Process the JSON response for each event
    for event in json_data['data']['events']:  # Iterate over each event
        event_id = event['id']
        event_name = event['name']
        
        for market in event['markets']:  # Iterate over each market in the event
            market_name = market['name']
            
            for outcome in market['outcomes']:  # Iterate over outcomes for each market
                outcome_name = outcome['name']
                odds_decimal_value = outcome['prices'][0]['decimal']
                numerator = outcome['prices'][0]['numerator']
                denominator = outcome['prices'][0]['denominator']
                outcome_type = outcome['type']
                outcome_subtype = outcome['subType']
                
                # Append captured values to the respective lists
                event_ids.append(event_id)
                event_names.append(event_name)
                market_names.append(market_name)
                outcome_names.append(outcome_name)
                odds_decimal.append(odds_decimal_value)
                prices_numerator.append(numerator)
                prices_denominator.append(denominator)
                outcome_types.append(outcome_type)
                outcome_subtypes.append(outcome_subtype)

    # Create a temporary DataFrame for this batch and append it to all_data
    temp_df = pd.DataFrame({
        'event_id': event_ids,
        'Event Name': event_names,
        'Market Name': market_names,
        'Outcome Name': outcome_names,
        'Odds (Decimal)': odds_decimal,
        'Price Numerator': prices_numerator,
        'Price Denominator': prices_denominator,
        'Outcome Type': outcome_types,
        'Outcome SubType': outcome_subtypes
    })
    
    all_data.append(temp_df)
    
    # Wait between 1 and 3 seconds
    time.sleep(random.uniform(1, 3.001))

# Concatenate all individual DataFrames into a final DataFrame
final_df = pd.concat(all_data, ignore_index=True)

# Show the final DataFrame
print(final_df)

In [ ]:
# Perform the left join on 'event_id' to get 'sport' and 'group_name' from events_df
final_df = final_df.merge(final_matches_df[['event_id', 'sport', 'competition']], on='event_id', how='left')

# Display the updated final_df
print(final_df)

In [4]:
# # Get all offers for all matches of Football event_ids
# # Initialize an empty list to accumulate all data
# all_data = []

# # Loop over all event_ids in your matches_df
# for event_id in final_matches_df['event_id']:
#     url = f"https://content.toto.nl/content-service/api/v1/q/events-by-ids?eventIds={event_id}&includeChildMarkets=true&includeCollections=true&includePriorityCollectionChildMarkets=true&includePriceHistory=false&includeCommentary=true&includeIncidents=false&includeRace=false&includePools=false&includeNonFixedOdds=false&lang=nl-NL&channel=I"

#     payload = {}
#     headers = {
#         'accept': 'application/json',
#         'accept-language': 'en-US,en;q=0.9,nl;q=0.8',
#         'Cookie': 'incap_ses_1581_2280942=FvpNPI919nl1UsyZNNfwFR6GL2cAAAAA8yX5UHfYkaWD/ax05SY+Jg==; visid_incap_2280942=CzAo1Y6yTMa654jo8RfVRtBiL2cAAAAAQkIPAAAAAAAE7rpFtkP20364qTw5VQQQ'
#     }

#     response = requests.get(url, headers=headers, data=payload)
#     json_data = json.loads(response.text)

#     # Initialize empty lists to store the data for this event
#     event_ids = []
#     event_names = []
#     market_names = []
#     outcome_names = []
#     odds_decimal = []
#     prices_numerator = []
#     prices_denominator = []
#     outcome_types = []
#     outcome_subtypes = []

#     # Iterate over the events, markets, and outcomes
#     for event in json_data['data']['events']:  # Iterate over each event
#         event_id = event['id']
#         event_name = event['name']
        
#         for market in event['markets']:  # Iterate over each market in the event
#             market_name = market['name']
            
#             for outcome in market['outcomes']:  # Iterate over outcomes for each market
#                 outcome_name = outcome['name']
#                 odds_decimal_value = outcome['prices'][0]['decimal']
#                 numerator = outcome['prices'][0]['numerator']
#                 denominator = outcome['prices'][0]['denominator']
#                 outcome_type = outcome['type']
#                 outcome_subtype = outcome['subType']
                
#                 # Append captured values to the respective lists
#                 event_ids.append(event_id)
#                 event_names.append(event_name)
#                 market_names.append(market_name)
#                 outcome_names.append(outcome_name)
#                 odds_decimal.append(odds_decimal_value)
#                 prices_numerator.append(numerator)
#                 prices_denominator.append(denominator)
#                 outcome_types.append(outcome_type)
#                 outcome_subtypes.append(outcome_subtype)

#     # Create a temporary DataFrame for this batch
#     temp_df = pd.DataFrame({
#         'Event ID': event_ids,
#         'Event Name': event_names,
#         'Market Name': market_names,
#         'Outcome Name': outcome_names,
#         'Odds (Decimal)': odds_decimal,
#         'Price Numerator': prices_numerator,
#         'Price Denominator': prices_denominator,
#         'Outcome Type': outcome_types,
#         'Outcome SubType': outcome_subtypes
#     })
    
#     # Append the temporary DataFrame to the all_data list
#     all_data.append(temp_df)
#     time.sleep(random.uniform(1, 3.001))

# # Concatenate all individual DataFrames into a final DataFrame
# final_df = pd.concat(all_data, ignore_index=True)

# # Show the final DataFrame
# print(final_df)

KeyboardInterrupt: 

In [69]:
# Get all bets for 1 match

# import pandas as pd

# # Initialize empty lists to store the data
# event_ids = []
# event_names = []
# market_names = []
# outcome_names = []
# odds_decimal = []
# prices_numerator = []
# prices_denominator = []
# outcome_types = []
# outcome_subtypes = []

# # Iterate over the events, markets, and outcomes
# for event in json_data['data']['events']:  # Iterate over each event
#     event_id = event['id']
#     event_name = event['name']
    
#     for market in event['markets']:  # Iterate over each market in the event
#         market_name = market['name']
        
#         for outcome in market['outcomes']:  # Iterate over outcomes for each market
#             outcome_name = outcome['name']
#             odds_decimal_value = outcome['prices'][0]['decimal']
#             numerator = outcome['prices'][0]['numerator']
#             denominator = outcome['prices'][0]['denominator']
#             outcome_type = outcome['type']
#             outcome_subtype = outcome['subType']
            
#             # Append captured values to the respective lists
#             event_ids.append(event_id)
#             event_names.append(event_name)
#             market_names.append(market_name)
#             outcome_names.append(outcome_name)
#             odds_decimal.append(odds_decimal_value)
#             prices_numerator.append(numerator)
#             prices_denominator.append(denominator)
#             outcome_types.append(outcome_type)
#             outcome_subtypes.append(outcome_subtype)

# # Create a DataFrame with the collected data
# df = pd.DataFrame({
#     'Event ID': event_ids,
#     'Event Name': event_names,
#     'Market Name': market_names,
#     'Outcome Name': outcome_names,
#     'Odds (Decimal)': odds_decimal,
#     'Price Numerator': prices_numerator,
#     'Price Denominator': prices_denominator,
#     'Outcome Type': outcome_types,
#     'Outcome SubType': outcome_subtypes
# })

# # Show the DataFrame
# df

    Event ID         Event Name     Market Name  \
0    5537946  FC Twente vs Ajax     Draw No Bet   
1    5537946  FC Twente vs Ajax     Draw No Bet   
2    5537946  FC Twente vs Ajax    Dubbele Kans   
3    5537946  FC Twente vs Ajax    Dubbele Kans   
4    5537946  FC Twente vs Ajax    Dubbele Kans   
..       ...                ...             ...   
451  5537946  FC Twente vs Ajax  Match Specials   
452  5537946  FC Twente vs Ajax  Match Specials   
453  5537946  FC Twente vs Ajax  Match Specials   
454  5537946  FC Twente vs Ajax  Match Specials   
455  5537946  FC Twente vs Ajax  Match Specials   

                            Outcome Name  Odds (Decimal)  Price Numerator  \
0                                   Ajax            1.75                3   
1                              FC Twente            2.08               27   
2                     Gelijkspel of Ajax            1.42               21   
3                      FC Twente of Ajax            1.33               33   
4 